**You can access TEST-1.mp3 audio here.**

---

[Audio Link](https://drive.google.com/file/d/1ODHCbW7LjuTUxd0njylHHHObwQxQVK6D/view?usp=drive_link)


[Video Link](https://drive.google.com/file/d/1NFifPUnU2w6WZKyEXLyQjcn1lEXnupRt/view?usp=drive_link)

# **INSTALLING MODULES**

In [1]:
!pip install speechbrain==0.5.16
!pip install faster_whisper
!pip install pyannote.audio
!pip install whisper

  Using cached speechbrain-0.5.16-py3-none-any.whl.metadata (23 kB)
Using cached speechbrain-0.5.16-py3-none-any.whl (630 kB)
  Attempting uninstall: speechbrain
    Found existing installation: speechbrain 1.0.3
    Uninstalling speechbrain-1.0.3:
      Successfully uninstalled speechbrain-1.0.3
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
pyannote-audio 3.3.2 requires speechbrain>=1.0.0, but you have speechbrain 0.5.16 which is incompatible.
  Using cached speechbrain-1.0.3-py3-none-any.whl.metadata (24 kB)
Using cached speechbrain-1.0.3-py3-none-any.whl (864 kB)
  Attempting uninstall: speechbrain
    Found existing installation: speechbrain 0.5.16
    Uninstalling speechbrain-0.5.16:
      Successfully uninstalled speechbrain-0.5.16


# **IMPORT NECESSARY LIBRARIES**

In [2]:
import librosa
import traceback
from faster_whisper import WhisperModel
import torch
import whisper
import datetime
from pathlib import Path
import pandas as pd
import re
import time
import os
import numpy as np
from sklearn.cluster import AgglomerativeClustering, KMeans
from pyannote.audio.pipelines.speaker_verification import PretrainedSpeakerEmbedding
from pyannote.audio import Audio
from pyannote.core import Segment
import speechbrain
from scipy.spatial.distance import cdist
from sklearn.metrics.pairwise import cosine_similarity

DEBUG:speechbrain.utils.checkpoints:Registered checkpoint save hook for _speechbrain_save
DEBUG:speechbrain.utils.checkpoints:Registered checkpoint load hook for _speechbrain_load
DEBUG:speechbrain.utils.checkpoints:Registered checkpoint save hook for save
DEBUG:speechbrain.utils.checkpoints:Registered checkpoint load hook for load
DEBUG:speechbrain.utils.checkpoints:Registered checkpoint save hook for _save
DEBUG:speechbrain.utils.checkpoints:Registered checkpoint load hook for _recover


In [3]:
!tar -xvf wavs.tar.gz

speaker_A.wav
speaker_B.wav
speaker_C.wav
speaker_D.wav
speaker_E.wav
sample.wav
sample_noisy.wav


# **UPLOAD AUDIO**

In [5]:
# Get the path to the audio file in your colab notebook
audio_file_path = '/content/TEST-1.mp3'

# **.mp3 to .wav conversion**

*   Sample Rate - 16 KHz
*   Channel - 1 (mono)
*   Audio Codec - pcm_s16le





In [ ]:
# prompt: convert mp3 to wav format

# !ffmpeg -i "{audio_file_path}" "{audio_file_path[:-4]}.wav"
!ffmpeg -i "{audio_file_path}" -ar 16000 -ac 1 -c:a pcm_s16le "{audio_file_path[:-4]}.wav"



ffmpeg version 4.4.2-0ubuntu0.22.04.1 Copyright (c) 2000-2021 the FFmpeg developers
  built with gcc 11 (Ubuntu 11.2.0-19ubuntu1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.22.04.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libdav1d --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libjack --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librabbitmq --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libsrt --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvidstab --enable-libvorbis --enable-libvpx --enab

# ****SPEAKER DIARIZATION - USING WHISPER SEGMENTS AND AGGLOMERATIVE HIERARCHICAL CLUSTERING****

In [ ]:


whisper_models = ["tiny", "base", "small", "medium", "large-v1", "large-v2"]



embedding_model = PretrainedSpeakerEmbedding(
    "speechbrain/spkrec-ecapa-voxceleb",
    device=torch.device("cuda" if torch.cuda.is_available() else "cpu")
)


def convert_time(secs):
    return datetime.timedelta(seconds=round(secs))

def speech_to_text(audio_file, whisper_model):
    model = WhisperModel(whisper_model, compute_type="int8")
    time_start = time.time()

    try:
        # Get duration
        audio_data, sample_rate = librosa.load(audio_file, mono= True, sr=16000)
        duration = len(audio_data) / sample_rate  # Calculate duration

        # Transcribe audio
        options = dict(language='en', beam_size=5, best_of=5)
        transcribe_options = dict(task="transcribe", **options)
        segments_raw, info = model.transcribe(audio_file, **transcribe_options)

        # Convert back to original openai format
        segments = []
        for segment_chunk in segments_raw:
            chunk = {}
            chunk["start"] = segment_chunk.start
            chunk["end"] = segment_chunk.end
            segments.append(chunk)

    except Exception as e:
        raise RuntimeError("Error converting video to audio")

    try:
        # Create embedding
        def segment_embedding(segment):
          try:
              audio = Audio()
              start = segment["start"]
              end = min(duration, segment["end"])

              clip = Segment(start, end)
              waveform, sample_rate = audio.crop(audio_file, clip)

              embeddings = embedding_model(waveform[None])

              return embeddings
          except Exception as e:
              traceback.print_exc()
              raise RuntimeError("Error during segment embedding", e)


        # Create embedding
        embeddings = np.zeros(shape=(len(segments), 192))
        for i, segment in enumerate(segments):
            embeddings[i] = segment_embedding(segment)
        embeddings = np.nan_to_num(embeddings)


        # Assign speaker label
        best_num_speaker = 2
        clustering = AgglomerativeClustering(best_num_speaker).fit(embeddings)
        labels = clustering.labels_
        for i in range(len(segments)):
            segments[i]["speaker"] = 'SPEAKER ' + str(labels[i] + 1)

        # Make output
        objects = {
            'Start' : [],
            'End': [],
            'Speaker': [],
        }
        for (i, segment) in enumerate(segments):
            if i == 0 or segments[i - 1]["speaker"] != segment["speaker"]:
                objects['Start'].append(str(convert_time(segment["start"])))
                objects['Speaker'].append(segment["speaker"])
                if i != 0:
                    objects['End'].append(str(convert_time(segments[i - 1]["end"])))
        objects['End'].append(str(convert_time(segments[i - 1]["end"])))

        save_path = "/content/drive/MyDrive/deep-learning/speech/TEST-1.csv"
        df_results = pd.DataFrame(objects)
        df_results.to_csv(save_path)
        return df_results, save_path

    except Exception as e:
        # Print exception for debugging
        print("Exception occurred:", e)
        raise RuntimeError("Error Running inference with local model", e)


# Provide the path to your audio file
audio_file = "/content/drive/MyDrive/deep-learning/speech/TEST-1.wav"

# Set the Whisper model and number of speakers
selected_whisper_model = "base"

# Run the transcription
transcription_results, save_path = speech_to_text(audio_file, selected_whisper_model)

# Print the transcription results
print(transcription_results)
print(f"Transcription results saved at: {save_path}")

INFO:speechbrain.utils.fetching:Fetch hyperparams.yaml: Using symlink found at '/root/.cache/torch/pyannote/speechbrain/hyperparams.yaml'
INFO:speechbrain.utils.fetching:Fetch custom.py: Fetching from HuggingFace Hub 'speechbrain/spkrec-ecapa-voxceleb' if not cached
DEBUG:speechbrain.utils.parameter_transfer:Collecting files (or symlinks) for pretraining in /root/.cache/torch/pyannote/speechbrain.
INFO:speechbrain.utils.fetching:Fetch embedding_model.ckpt: Using symlink found at '/root/.cache/torch/pyannote/speechbrain/embedding_model.ckpt'
DEBUG:speechbrain.utils.parameter_transfer:Set local path in self.paths["embedding_model"] = /root/.cache/torch/pyannote/speechbrain/embedding_model.ckpt
INFO:speechbrain.utils.fetching:Fetch mean_var_norm_emb.ckpt: Using symlink found at '/root/.cache/torch/pyannote/speechbrain/mean_var_norm_emb.ckpt'
DEBUG:speechbrain.utils.parameter_transfer:Set local path in self.paths["mean_var_norm_emb"] = /root/.cache/torch/pyannote/speechbrain/mean_var_norm_

     Start      End    Speaker
0  0:00:00  0:00:04  SPEAKER 2
1  0:00:04  0:00:27  SPEAKER 1
2  0:00:27  0:00:31  SPEAKER 2
3  0:00:31  0:00:54  SPEAKER 1
4  0:00:54  0:00:57  SPEAKER 2
5  0:00:57  0:01:22  SPEAKER 1
6  0:01:22  0:01:27  SPEAKER 2
7  0:01:27  0:01:58  SPEAKER 1
Transcription results saved at: /content/drive/MyDrive/deep-learning/speech/TEST-1.csv


In [ ]:
!pip install moviepy pandas pillow

In [ ]:
import pandas as pd
from moviepy.editor import VideoFileClip, ImageClip, CompositeVideoClip
from PIL import Image, ImageDraw, ImageFont



df_results = transcription_results

# Step 4: Load the Video
video_path = '/content/drive/MyDrive/deep-learning/speech/videoplayback_test1.mp4'  # Update with your video path
video = VideoFileClip(video_path)

# Function to create an image with text
def create_text_image(text, font_size=70, img_size=(640, 80), bg_color=(0, 0, 0), text_color=(255, 255, 255)):
    img = Image.new('RGB', img_size, color=bg_color)
    d = ImageDraw.Draw(img)
    try:
        font = ImageFont.truetype("arial.ttf", font_size)
    except IOError:
        font = ImageFont.load_default()
    # Use textbbox instead of textsize
    bbox = d.textbbox((0, 0), text, font=font)
    text_width = bbox[2] - bbox[0]
    text_height = bbox[3] - bbox[1]

    position = ((img_size[0]-text_width)/2, (img_size[1]-text_height)/2)
    d.text(position, text, fill=text_color, font=font)
    return img

# Step 5: Overlay Speaker Labels
clips = [video]

for _, row in df_results.iterrows():
    start_time = pd.to_datetime(row['Start']).time()
    end_time = pd.to_datetime(row['End']).time()

    start_seconds = start_time.hour * 3600 + start_time.minute * 60 + start_time.second
    end_seconds = end_time.hour * 3600 + end_time.minute * 60 + end_time.second

    text_img = create_text_image(row['Speaker'])
    text_img_path = '/content/drive/MyDrive/deep-learning/speech/temp_text_img.png'
    text_img.save(text_img_path)

    txt_clip = (ImageClip(text_img_path)
                .set_position(('center', 'bottom'))
                .set_start(start_seconds)
                .set_duration(end_seconds - start_seconds))

    clips.append(txt_clip)

# Combine all clips
final_video = CompositeVideoClip(clips)

# Step 6: Save the Modified Video
final_video_path = '/content/drive/MyDrive/deep-learning/speech/videoplayback_label.mp4'
final_video.write_videofile(final_video_path, codec='libx264')

Moviepy - Building video /content/drive/MyDrive/deep-learning/speech/videoplayback_label.mp4.
MoviePy - Writing audio in videoplayback_labelTEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video /content/drive/MyDrive/deep-learning/speech/videoplayback_label.mp4



Moviepy - Done !
Moviepy - video ready /content/drive/MyDrive/deep-learning/speech/videoplayback_label.mp4


In [ ]:
# @title
from IPython.display import HTML
from base64 import b64encode

def show_video(final_video_path, video_width = 1000):

  video_file = open(final_video_path, "r+b").read()

  video_url = f"data:video/mp4;base64,{b64encode(video_file).decode()}"
  return HTML(f"""<video width={video_width} controls><source src="{video_url}"></video>""")

show_video(final_video_path)

# **ASSIGNMENT**


# **HELPER FUNCTIONS**

In [62]:
# Purpose: This function is for converting time in seconds into a human-readable format,
# specifically  'hh:mm:ss'
# Input: It takes a floating-point number representing time in seconds
# Output: It should return a string representing the time in 'hh:mm:ss'
def convert_time(secs):
  return datetime.timedelta(seconds=round(secs))

In [63]:
# Purpose: This function handles the audio transcription process using the
# Output: Return a list of segment dictionaries.
def transcribe_audio(audio_file, model_name="base", language="en", beam_size=5, best_of=5):
  # Load the model
  model = WhisperModel(model_name, compute_type='int8')
  start_time = time.time()

  try:
    # Transcribe audio
    options = dict(language='en', beam_size=5, best_of=5)
    transcribe_options = dict(task='transcribe', **options)
    segments_raw, info = model.transcribe(audio_file, **transcribe_options)

    # Convert back to original openai format
    segments = []
    for segment_chunk in segments_raw:
      chunk = {}
      chunk['start'] = segment_chunk.start
      chunk['end'] = segment_chunk.end
      chunk['text'] = segment_chunk.text
      segments.append(chunk)

  except Exception as e:
    raise RuntimeError(f"Error converting audio to transcribe.{e}")

  return segments


In [64]:
# Purpose: This function extracts a speaker embedding for a specific segment of
# an audio file using a pre-trained speaker embedding model.
def extract_segment_embedding(audio_file, segment, total_duration,
                              embedding_model):
  try:
    audio = Audio()
    start = segment['start']
    end = min(total_duration, segment['end']) # end time cannot more than t_d

    clip = Segment(start, end)
    # method to extract the waveform for the given segment from the
    waveform, sample_rate = audio.crop(audio_file, clip)

    embeddings = embedding_model(waveform[None])

    return embeddings.squeeze()
  except Exception as e:
    traceback.print_exc()
    raise RuntimeError(f"Error during segment embedding {e}")

In [65]:
def compute_segment_embeddings(audio_file, segments, embedding_model):
  audio_data, sample_rate = librosa.load(audio_file, mono=True, sr=16000)
  total_duration = len(audio_data)/sample_rate

  # get embeddings for each segments
  embeddings = []
  for segment in segments:
    embeddings.append(extract_segment_embedding(audio_file, segment, total_duration, embedding_model))

  embedding_vec = np.stack(embeddings)
  embedding_vec = np.nan_to_num(embedding_vec)

  return embedding_vec

In [66]:
def cluster_embeddings(embeddings, n_clusters):
  # Initialize KMeans cluster
  kmeans = KMeans(
      n_clusters=n_clusters,
      random_state=42
  )

  kmeans.fit(embeddings)
  labels = kmeans.labels_

  centroids = kmeans.cluster_centers_

  return labels, centroids


In [67]:
# Purpose: Calculate the average embedding for each cluster. This average embedding represents a
# cluster's speaker profile.
def compute_cluster_averages(embeddings, labels, n_clusters):
  avg_cluster_labels = {}
  for i in range(n_clusters):
    cluster_masked = (labels==i)
    masked_embeddings = embeddings[cluster_masked]
    avg_embedding = np.mean(masked_embeddings, axis=0)
    avg_cluster_labels[i]=avg_embedding
  return avg_cluster_labels

In [68]:
# Purpose: To load audio files of known speakers, compute their speaker embeddings, and store them for speaker identification.
def load_known_speaker_embeddings(known_speaker_files, embedding_model):
  known_speaker = {}
  for f_name in known_speaker_files:
    audio_data, sample_rate = librosa.load(f_name, mono=True, sr=16000)
    audio = Audio()
    total_duration = len(audio_data)/sample_rate
    clip = Segment(0, total_duration)

    waveform, sample_rate = audio.crop(f_name, clip)

    embeddings = embedding_model(waveform[None])
    embeddings = embeddings.squeeze()
    known_speaker[f_name.split('.')[0]]=embeddings

  return known_speaker

In [81]:
def assign_speaker_labels(cluster_avg_embeddings, known_speaker_embeddings, similarity_threshold=0.7):
    speaker_labels = {}
    best_consine_similarity_score = []
    for cluster_id, avg_emb in cluster_avg_embeddings.items():
        max_sim = -1
        best_label = "Unknown"

        for spk_label, spk_emb in known_speaker_embeddings.items():
            # Compute cosine similarity
            cos_sim = cosine_similarity(avg_emb.reshape(1, -1), spk_emb.reshape(1, -1))[0][0]

            if cos_sim > max_sim:
                max_sim = cos_sim
                best_label = spk_label

        best_consine_similarity_score.append(max_sim)
        print(cluster_id, best_label)
        print(f"Best consine similarity scores of the clusters {best_consine_similarity_score}")
        print(f"Average of these best {round(sum(best_consine_similarity_score)/3,3)}")
        # Apply threshold
        if max_sim >= similarity_threshold:
            speaker_labels[cluster_id] = best_label
        else:
            speaker_labels[cluster_id] = "Unknown"

    return speaker_labels

In [70]:
# Purpose: This function orchestrates the entire speaker diarization and identification pipeline, calling all the previously defined functions in the correct sequence.
def run_pipeline(audio_file, embedding_model, known_speaker_embeddings, n_clusters=3, whisper_model_name="base", similarity_threshold=0.7):
  print('#'*40)
  print("Started Diarization and Identification Pipeline")
  # Get the segments of the audio
  segments = transcribe_audio(audio_file)
  # Get the segments vector
  embedding_vec = compute_segment_embeddings(audio_file, segments, embedding_model)
  # Get the labels and centroids for each cluster
  labels, centroids = cluster_embeddings(embedding_vec, n_clusters)
  # Computer cluster avetages
  cluster_avg_embeddings = compute_cluster_averages(embedding_vec, labels, n_clusters)
  # Get the labels for the speakers in the cluster
  speaker_labels = assign_speaker_labels(cluster_avg_embeddings, known_speaker_embeddings, similarity_threshold)

  # Annotate each segment with its cluster ID and assigned speaker ID.
  results = []
  for segment, cluster_id in zip(segments, labels):
      start = segment['start']
      end = segment['end']
      speaker_id = speaker_labels.get(cluster_id)
      results.append({
          'Start': convert_time(start),
          'End': convert_time(end),
          'Test': segment['text'],
          'Cluster': cluster_id,
          'Speaker_ID': speaker_id
      })

  df = pd.DataFrame(results)
  print(df)
  return df, len(segments), centroids

# **LOADING MODELS AND DATA**

In [71]:
embedding_model = PretrainedSpeakerEmbedding(
    "speechbrain/spkrec-ecapa-voxceleb",
    device=torch.device("cuda" if torch.cuda.is_available() else "cpu")
)

INFO:speechbrain.utils.fetching:Fetch hyperparams.yaml: Using symlink found at '/root/.cache/torch/pyannote/speechbrain/hyperparams.yaml'
INFO:speechbrain.utils.fetching:Fetch custom.py: Fetching from HuggingFace Hub 'speechbrain/spkrec-ecapa-voxceleb' if not cached
DEBUG:speechbrain.utils.parameter_transfer:Collecting files (or symlinks) for pretraining in /root/.cache/torch/pyannote/speechbrain.
INFO:speechbrain.utils.fetching:Fetch embedding_model.ckpt: Using symlink found at '/root/.cache/torch/pyannote/speechbrain/embedding_model.ckpt'
DEBUG:speechbrain.utils.parameter_transfer:Set local path in self.paths["embedding_model"] = /root/.cache/torch/pyannote/speechbrain/embedding_model.ckpt
INFO:speechbrain.utils.fetching:Fetch mean_var_norm_emb.ckpt: Using symlink found at '/root/.cache/torch/pyannote/speechbrain/mean_var_norm_emb.ckpt'
DEBUG:speechbrain.utils.parameter_transfer:Set local path in self.paths["mean_var_norm_emb"] = /root/.cache/torch/pyannote/speechbrain/mean_var_norm_

In [72]:
known_speaker_files = ['sample.wav', 'sample_noisy.wav', 'speaker_A.wav', 'speaker_B.wav', 'speaker_C.wav', 'speaker_D.wav', 'speaker_E.wav']

In [73]:
known_speakers = load_known_speaker_embeddings(known_speaker_files, embedding_model)

# **PROCESSING AUDIO SAMPLES**

In [74]:
round(sum([np.float32(0.68920267), np.float32(0.79727113), np.float32(0.85755897)])/3, 3)

np.float32(0.781)

In [82]:
clean_audio = 'sample.wav'
df_clean, n_segments_clean, centroids_clean = run_pipeline(clean_audio, embedding_model, known_speakers, 3, 'base', 0.7)

########################################
Started Diarization and Identification Pipeline
0 speaker_A
Best consine similarity scores of the clusters [np.float32(0.68920267)]
Average of these best 0.23000000417232513
1 speaker_C
Best consine similarity scores of the clusters [np.float32(0.68920267), np.float32(0.79727113)]
Average of these best 0.4950000047683716
2 speaker_B
Best consine similarity scores of the clusters [np.float32(0.68920267), np.float32(0.79727113), np.float32(0.85755897)]
Average of these best 0.781000018119812
            Start             End  \
0 0 days 00:00:00 0 days 00:00:06   
1 0 days 00:00:08 0 days 00:00:14   
2 0 days 00:00:15 0 days 00:00:17   
3 0 days 00:00:18 0 days 00:00:24   
4 0 days 00:00:25 0 days 00:00:29   
5 0 days 00:00:31 0 days 00:00:36   

                                                Test  Cluster Speaker_ID  
0   This device picked up the same amount of musk...        2  speaker_B  
1   Raising front-down would likely produce simil...  

# **PROCESSING NOISY AUDIO SAMPLES**

In [80]:
noisy_audio = 'sample_noisy.wav'
df_noisy, n_segments_noisy, centroids_noisy = run_pipeline(noisy_audio, embedding_model, known_speakers, 3, 'base', 0.65)

########################################
Started Diarization and Identification Pipeline
Best consine similarity scores of the clusters [np.float32(0.5812957)]
Average of these best 0.1940000057220459
Best consine similarity scores of the clusters [np.float32(0.5812957), np.float32(0.547127)]
Average of these best 0.37599998712539673
Best consine similarity scores of the clusters [np.float32(0.5812957), np.float32(0.547127), np.float32(0.6756178)]
Average of these best 0.6010000109672546
            Start             End  \
0 0 days 00:00:00 0 days 00:00:05   
1 0 days 00:00:08 0 days 00:00:13   
2 0 days 00:00:15 0 days 00:00:17   
3 0 days 00:00:18 0 days 00:00:21   
4 0 days 00:00:21 0 days 00:00:23   
5 0 days 00:00:25 0 days 00:00:27   
6 0 days 00:00:27 0 days 00:00:29   
7 0 days 00:00:30 0 days 00:00:35   

                                                Test  Cluster Speaker_ID  
0   This device picked up the same amount of must...        2  speaker_B  
1   Raising fine sand i

# **1.**

# **5.**

In [77]:
df_clean.head(10)

Start             End  \
0 0 days 00:00:00 0 days 00:00:06   
1 0 days 00:00:08 0 days 00:00:14   
2 0 days 00:00:15 0 days 00:00:17   
3 0 days 00:00:18 0 days 00:00:24   
4 0 days 00:00:25 0 days 00:00:29   
5 0 days 00:00:31 0 days 00:00:36   

                                                Test  Cluster Speaker_ID  
0   This device picked up the same amount of musk...        2  speaker_B  
1   Raising front-down would likely produce simil...        1  speaker_C  
2                                Do you doubt Homer?        0    Unknown  
3   One can also build cords by stacking fifths y...        1  speaker_C  
4   Forget Apollo, he said, with his suggestion o...        0    Unknown  
5   Biconical bots with cylindrical necks are esp...        2  speaker_B

In [78]:
df_noisy.head(20)

Start             End  \
0 0 days 00:00:00 0 days 00:00:05   
1 0 days 00:00:08 0 days 00:00:13   
2 0 days 00:00:15 0 days 00:00:17   
3 0 days 00:00:18 0 days 00:00:21   
4 0 days 00:00:21 0 days 00:00:23   
5 0 days 00:00:25 0 days 00:00:27   
6 0 days 00:00:27 0 days 00:00:29   
7 0 days 00:00:30 0 days 00:00:35   

                                                Test  Cluster Speaker_ID  
0   This device picked up the same amount of must...        2    Unknown  
1   Raising fine sand is likely to be a scenario ...        1    Unknown  
2                                Do you doubt Homan?        0    Unknown  
3        One can also build cores by striking fifth.        1    Unknown  
4                       You have been control Homan.        1    Unknown  
5                          Forget a follow, he said.        0    Unknown  
6         With his suggestion of severity and voice.        0    Unknown  
7   Biconical bots with cylindrical necks are esp...        2    Unknown

In [79]:
round((df_noisy.shape[0]-df_clean.shape[0])/df_clean.shape[0]*100, 2)

33.33